# Horse collar data exploration

<img align="right" src="https://anitagraser.github.io/movingpandas/pics/movingpandas.png">

This notebook presents a systematic movement data exploration workflow. 
The proposed workflow consists of five main steps:

1. **Establishing an overview** by visualizing raw input data records
2. **Putting records in context** by exploring information from consecutive movement data records (such as: time between records, speed, and direction)
3. **Extracting trajectories, locations & events** by dividing the raw continuous tracks into individual trajectories, locations, and events
4. **Exploring patterns** in trajectory and event data by looking at groups of the trajectories or events
5. **Analyzing outliers** by looking at potential outliers and how they may challenge preconceived assumptions about the dataset characteristics

The workflow is demonstrated using horse collar tracking data provided by Prof. Lene Fischer (University of Copenhagen) and the Center for Technology & Environment of Guldborgsund Municiplaity in Denmark but should be generic enough to be applied to other tracking datasets.

The workflow is implemented in Python using Pandas, GeoPandas, and MovingPandas (http://movingpandas.org).

For an interactive version of this notebook visit https://mybinder.org/v2/gh/anitagraser/movingpandas/master.

## Setup

In [1]:
%matplotlib inline

In [2]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [3]:
import urllib
import os
import numpy as np
import pandas as pd
import geopandas as gpd
from geopandas import GeoDataFrame, read_file
from datetime import datetime, timedelta
from pyproj import CRS

import sys
sys.path.append("..")
import movingpandas as mpd

import warnings
warnings.simplefilter("ignore")

import hvplot.pandas # seems to be necessary for the following import to work
from holoviews import opts
opts.defaults(opts.Overlay(active_tools=['wheel_zoom']))

## Raw data import

In [4]:
df = read_file('../data/horse_collar.gpkg')
df['t'] = pd.to_datetime(df['timestamp'])
df = df.set_index('t').tz_localize(None)
print("This dataset contains {} records.\nThe first lines are:".format(len(df)))
df.head()

This dataset contains 17517 records.
The first lines are:


No  CollarID    UTC_Date  UTC_Time    LMT_Date  \
t                                                                      
2018-11-14 12:01:08  299     30788  14-11-2018  12:01:08  14-11-2018   
2018-11-14 12:15:09  300     30788  14-11-2018  12:15:09  14-11-2018   
2018-11-14 12:30:08  301     30788  14-11-2018  12:30:08  14-11-2018   
2018-11-14 13:00:33  302     30788  14-11-2018  13:00:33  14-11-2018   
2018-11-14 13:30:09  303     30788  14-11-2018  13:30:09  14-11-2018   

                     LMT_Time Origin   SCTS_Date SCTS_Time  Latitude [?]  ...  \
t                                                                         ...   
2018-11-14 12:01:08  12:01:08    GSM  14-11-2018  14:32:31     547433308  ...   
2018-11-14 12:15:09  12:15:09    GSM  14-11-2018  14:32:31     546768844  ...   
2018-11-14 12:30:08  12:30:08    GSM  14-11-2018  14:32:31     546270178  ...   
2018-11-14 13:00:33  13:00:33    GSM  14-11-2018  14:32:31     546258926  ...   
2018-11-14 13:30:09  13:30:09    GSM  14-11-2018  14:32:31     546261709  ...   

                     C/N_10  Sat_11  C/N_11 Mort. Status  Temp [?C]  Activity  \
t                                                                               
2018-11-14 12:01:08    None    None    None         None       22.0      None   
2018-11-14 12:15:09    None    None    None         None       22.0      None   
2018-11-14 12:30:08    None    None    None         None       21.0      None   
2018-11-14 13:00:33    None    None    None         None       17.0      None   
2018-11-14 13:30:09    None    None    None         None       17.0      None   

                            Easting       Northing            timestamp  \
t                                                                         
2018-11-14 12:01:08  32.687.757.575  6.070.134.340  2018-11-14 12:01:08   
2018-11-14 12:15:09  32.687.671.089  6.062.727.428  2018-11-14 12:15:09   
2018-11-14 12:30:08  32.690.932.613  6.057.307.713  2018-11-14 12:30:08   
2018-11-14 13:00:33  32.690.669.041  6.057.171.253  2018-11-14 13:00:33   
2018-11-14 13:30:09  32.690.706.054  6.057.203.820  2018-11-14 13:30:09   

                                           geometry  
t                                                    
2018-11-14 12:01:08  POINT (687757.574 6070134.334)  
2018-11-14 12:15:09  POINT (687671.088 6062727.428)  
2018-11-14 12:30:08  POINT (690932.614 6057307.716)  
2018-11-14 13:00:33  POINT (690669.038 6057171.248)  
2018-11-14 13:30:09  POINT (690706.056 6057203.814)  

[5 rows x 48 columns]

In [5]:
df.columns

Index(['No', 'CollarID', 'UTC_Date', 'UTC_Time', 'LMT_Date', 'LMT_Time',
       'Origin', 'SCTS_Date', 'SCTS_Time', 'Latitude [?]', 'Longitude [?]',
       'lat', 'long', 'FixType', 'Main [V]', 'Beacon [V]', 'Sats', 'Sat',
       'C/N', 'Sat_1', 'C/N_1', 'Sat_2', 'C/N_2', 'Sat_3', 'C/N_3', 'Sat_4',
       'C/N_4', 'Sat_5', 'C/N_5', 'Sat_6', 'C/N_6', 'Sat_7', 'C/N_7', 'Sat_8',
       'C/N_8', 'Sat_9', 'C/N_9', 'Sat_10', 'C/N_10', 'Sat_11', 'C/N_11',
       'Mort. Status', 'Temp [?C]', 'Activity', 'Easting', 'Northing',
       'timestamp', 'geometry'],
      dtype='object')

In [6]:
df = df.drop(columns=['LMT_Date', 'LMT_Time',
       'Origin', 'SCTS_Date', 'SCTS_Time', 'Latitude [?]', 'Longitude [?]',
       'FixType', 'Main [V]', 'Beacon [V]', 'Sats', 'Sat',
       'C/N', 'Sat_1', 'C/N_1', 'Sat_2', 'C/N_2', 'Sat_3', 'C/N_3', 'Sat_4',
       'C/N_4', 'Sat_5', 'C/N_5', 'Sat_6', 'C/N_6', 'Sat_7', 'C/N_7', 'Sat_8',
       'C/N_8', 'Sat_9', 'C/N_9', 'Sat_10', 'C/N_10', 'Sat_11', 'C/N_11',
       'Easting', 'Northing',], axis=1)

In [7]:
df.head()

No  CollarID    UTC_Date  UTC_Time        lat  \
t                                                                     
2018-11-14 12:01:08  299     30788  14-11-2018  12:01:08  54.743331   
2018-11-14 12:15:09  300     30788  14-11-2018  12:15:09  54.676884   
2018-11-14 12:30:08  301     30788  14-11-2018  12:30:08  54.627018   
2018-11-14 13:00:33  302     30788  14-11-2018  13:00:33  54.625893   
2018-11-14 13:30:09  303     30788  14-11-2018  13:30:09  54.626171   

                          long Mort. Status  Temp [?C] Activity  \
t                                                                 
2018-11-14 12:01:08  11.916987         None       22.0     None   
2018-11-14 12:15:09  11.910876         None       22.0     None   
2018-11-14 12:30:08  11.957852         None       21.0     None   
2018-11-14 13:00:33  11.953686         None       17.0     None   
2018-11-14 13:30:09  11.954280         None       17.0     None   

                               timestamp                        geometry  
t                                                                         
2018-11-14 12:01:08  2018-11-14 12:01:08  POINT (687757.574 6070134.334)  
2018-11-14 12:15:09  2018-11-14 12:15:09  POINT (687671.088 6062727.428)  
2018-11-14 12:30:08  2018-11-14 12:30:08  POINT (690932.614 6057307.716)  
2018-11-14 13:00:33  2018-11-14 13:00:33  POINT (690669.038 6057171.248)  
2018-11-14 13:30:09  2018-11-14 13:30:09  POINT (690706.056 6057203.814)

In [8]:
collar_id = df['CollarID'].unique()[0]
print("There is only one collar with ID {}.".format(collar_id))

There is only one collar with ID 30788.


In [9]:
df['Activity'].unique()

array([None], dtype=object)

In [10]:
original_crs = df.crs
original_crs

<Projected CRS: EPSG:25832>
Name: ETRS89 / UTM zone 32N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Europe - 6°E to 12°E and ETRS89 by country
- bounds: (6.0, 38.76, 12.0, 83.92)
Coordinate Operation:
- name: UTM zone 32N
- method: Transverse Mercator
Datum: European Terrestrial Reference System 1989
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

## 1. Establishing an overview

The ﬁrst step in our proposed EDA workﬂow can be performed directly on raw
input data since it does not require temporally ordered data. It is therefore suitable
as a ﬁrst exploratory step when dealing with new data.

### Q1.1 Geographic extent: Is the geographical extent as expected and are there holes in the spatial coverage?

In [11]:
df.to_crs({'init': 'epsg:4326'}).hvplot(title='Geographic extent of the dataset', geo=True, tiles='OSM', width=500, height=500)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]

The main area (the horste's pasture?) is located south of Nykobing Strandhuse.

However, we find also find two records on the road north west of the main area. Both points have been recorded on 2018-11-14 which is the first day of the dataset.

In [12]:
pd.DataFrame(df).sort_values('lat').tail(2)

No  CollarID    UTC_Date  UTC_Time        lat  \
t                                                                     
2018-11-14 12:15:09  300     30788  14-11-2018  12:15:09  54.676884   
2018-11-14 12:01:08  299     30788  14-11-2018  12:01:08  54.743331   

                          long Mort. Status  Temp [?C] Activity  \
t                                                                 
2018-11-14 12:15:09  11.910876         None       22.0     None   
2018-11-14 12:01:08  11.916987         None       22.0     None   

                               timestamp                        geometry  
t                                                                         
2018-11-14 12:15:09  2018-11-14 12:15:09  POINT (687671.088 6062727.428)  
2018-11-14 12:01:08  2018-11-14 12:01:08  POINT (687757.574 6070134.334)

A potential hypothesis for the origin of these two records is that the horse (or the collar) was transported on 2018-11-14, taking the road from Nykobing Falster south to the pasture.

If we remove these first two records from the dataset, the remainder of the records are located in a small area:

In [13]:
df = df[2:].to_crs({'init': 'epsg:4326'})
( df.hvplot(title='OSM showing paths and fences', size=2, geo=True, tiles='OSM', width=500, height=500) +
  df.hvplot(title='Imagery showing land cover details', size=2, color='red', geo=True, tiles='EsriImagery', width=500, height=500) )

:Layout
   .Overlay.I  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.II :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]

It looks like the horse generally avoids areas without green vegetation since point patterns in these area appear more sparse than in other areas.

In [14]:
temp = df.to_crs(CRS(25832))
temp['geometry'] = temp['geometry'].buffer(5)
total_area = temp.dissolve(by='CollarID').area 
total_area = total_area[collar_id]/10000
print('The total area covered by the data is: {:,.2f} ha'.format(total_area))

The total area covered by the data is: 65.19 ha


### Q1.2 Temporal extent: Is the temporal extent as expected and are there holes in the temporal coverage?

In [15]:
print("The dataset covers the time between {} and {}.".format(df.index.min(), df.index.max()))

The dataset covers the time between 2018-11-14 12:30:08 and 2019-11-07 05:30:10.


In [16]:
print("That's {}".format(df.index.max() - df.index.min()))

That's 357 days 17:00:02


In [17]:
df['No'].resample('1d').count().hvplot(title='Number of records per day')

:Curve   [t]   (No)

On most days there are 48 (+/- 1) records per day. However, there are some days with more records (in Nov 2018 and later between Mai and August 2019). 

There is one gap: On 2019-10-18 there are no records in the dataset and the previous day only contains 37 and the following day 27 records.

### Q1.3 Spatio-temporal gaps: Does the geographic extent vary over time or do holes appear during certain times? 

Considering that the dataset covers a whole year, it may be worthwhile to look at the individual months using small multiples map plots, for example:

In [18]:
df['Y-M'] = df.index.to_period('M')
a = None
for i in df['Y-M'].unique():
    plot = df[df['Y-M']==i].hvplot(title=str(i), size=2, geo=True, tiles='OSM', width=300, height=300)
    if a: a = a + plot
    else: a = plot
a

:Layout
   .Overlay.I    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.II   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.III  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.IV   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.V    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VI   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VII  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VIII :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.IX   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.X    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.XI   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.XII  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.XIII :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]

The largest change between months seems to be that the southernmost part of the pasture wasn't used in August and September 2019. 

## 2. Putting records in context

The second exploration step puts movement records in their temporal and geographic
context. The exploration includes information based on consecutive movement data
records, such as time between records (sampling intervals), speed, and direction.
Therefore, this step requires temporally ordered data. 

### Q2.1 Sampling intervals: Is the data sampled at regular or irregular intervals?

For example, tracking data of migratory animals is expected to exhibit seasonal changes. Such changes in vehicle tracking systems however may indicate issues with data collection .

In [19]:
t = df.reset_index().t
df = df.assign(delta_t=t.diff().values)
df['delta_t'] = df['delta_t'].dt.total_seconds()/60
pd.DataFrame(df).hvplot.hist('delta_t', title='Histogram of intervals between consecutive records (in minutes)', bins=60, bin_range=(0, 60))

:Histogram   [delta_t]   (delta_t_count)

The time delta between consecutive records is usually around 30 minutes. 

However, it seems that sometimes the intererval has been decreased to around 15 minutes. This would explain why some days have more than the usual 48 records. 

### Q2.2 Speed values: Are there any unrealistic movements? 

For example: Does the data contain unattainable speeds?

In [20]:
tc = mpd.TrajectoryCollection(df, 'CollarID')
traj = tc.trajectories[0]
traj.add_speed()
max_speed = traj.df.speed.max()
print("The highest computed speed is {:,.2f} m/s ({:,.2f} km/h)".format(max_speed, max_speed*3600/1000))

The highest computed speed is 0.81 m/s (2.93 km/h)


### Q2.3 Movement patterns: Are there any patterns in movement direction or speed?

In [21]:
pd.DataFrame(traj.df).hvplot.hist('speed', title='Histogram of speeds (in meters per second)', bins=90)

:Histogram   [speed]   (speed_count)

The speed distribution shows no surprising patterns.

In [22]:
traj.add_direction(overwrite=True)
pd.DataFrame(traj.df).hvplot.hist('direction', title='Histogram of directions', bins=90)

:Histogram   [direction]   (direction_count)

There is some variation in movement directions but no directions stand out in the histogram.

Let's look at spatial patterns of direction and speed!


### Q2.4 Temporal context: Does the movement make sense in its temporal context? 

For example: Do nocturnal animal tracks show movement at night?


In [23]:
pd.DataFrame(traj.df).hvplot.heatmap(title='Mean speed by hour of day and month of year', 
                                     x='t.hour', y='t.month', C='speed', reduce_function=np.mean)

:HeatMap   [t.hour,t.month]   (speed)

The movement speed by hour of day shows a clear pattern throughout the year with earlier and longer fast movements during the summer months and later and slower movements during the winter months. 

#### Temperature context

In addition to time, the dataset also contains temperature information for each record:

In [24]:
traj.df['n'] = 1
pd.DataFrame(traj.df).hvplot.heatmap(title='Record count by temperature and month of year', 
                                     x='Temp [?C]', y='t.month', C='n', reduce_function=np.sum)

:HeatMap   [Temp [?C],t.month]   (n)

In [25]:
pd.DataFrame(traj.df).hvplot.heatmap(title='Mean speed by temperature and month of year', 
                                     x='Temp [?C]', y='t.month', C='speed', reduce_function=np.mean)

:HeatMap   [Temp [?C],t.month]   (speed)

### Q2.5 Geographic context: Does the movement make sense in its geographic context? 

For example: Do vessels follow traﬃc separation schemes deﬁned in maritime maps? Are there any ship trajectories crossing land?

In [26]:
traj.df['dir_class'] = ((traj.df['direction']-22.5)/45).round(0)

a = None
temp = traj.df
for i in sorted(temp['dir_class'].unique()):
    plot = temp[temp['dir_class']==i].hvplot(geo=True, tiles='OSM', size=2, width=300, height=300, title=str(int(i*45))+"°")
    if a: a = a + plot
    else: a = plot
a

:Layout
   .Overlay.I    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.II   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.III  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.IV   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.V    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VI   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VII  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VIII :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]

There are no obvious spatial movement direction patterns.

In [27]:
traj.df['speed_class'] = (traj.df['speed']*2).round(1)

a = None
temp = traj.df
for i in sorted(temp['speed_class'].unique()):
    filtered = temp[temp['speed_class']==i]
    if len(filtered) < 10: 
        continue
    plot = filtered.hvplot(geo=True, tiles='EsriImagery', color='red', size=2, width=300, height=300, title=str(i/2)) # alpha=max(0.05, 50/len(filtered)), 
    if a: a = a + plot
    else: a = plot
a

:Layout
   .Overlay.I    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.II   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.III  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.IV   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.V    :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VI   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VII  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.VIII :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]

Low speed records (classes 0.0 and 0.05 m/s) are distributed over the whole area with many points on the outline (fence?) of the area. 

Medium speed records (classes 0.1 and 0.15 m/s) seem to be more common along paths and channels. 

## 3. Extracting trajectories & locations / events

The third exploration step looks at individual trajectories. It therefore requires that
the continuous tracks are split into individual trajectories. Analysis results depend on
how the continuous streams are divided into trajectories, locations, and events. 

### 3.1 Trajectory lines: Do the trajectory lines look plausible or are there indications of out of sequence positions or other unrealistic location jumps?

In [28]:
tc.hvplot() 

:Overlay
   .Tiles.I :Tiles   [x,y]
   .Path.I  :Path   [Longitude,Latitude]

Due to the 30 minute reporting interval, the trajectories are rather sparse. 

The trajectories mostly stay within the (fenced?) area. However, there are a few cases of positions outside the area.

#### Movement during week #1

In [29]:
daily = mpd.TemporalSplitter(tc).split(mode='day')

In [30]:
a = None
for i in range(0,7):
    if a: a = a + daily.trajectories[i].hvplot(title=daily.trajectories[i].id, c='speed', line_width=2, cmap='RdYlBu', width=300, height=300)
    else: a = daily.trajectories[i].hvplot(title=daily.trajectories[i].id, c='speed', line_width=2, cmap='RdYlBu', width=300, height=300)
a

:Layout
   .Overlay.I   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.II  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.III :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.IV  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.V   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.VI  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.VII :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)

### 3.2 Home/depot locations: Do day trajectories start and end at the same home (for human and animal movement) or depot (for logistics applications) location?

In [31]:
daily_starts = daily.get_start_locations()
daily_starts['month'] = daily_starts.index.month
daily_starts.hvplot(c='month', geo=True, tiles='EsriImagery', cmap='autumn', width=500, height=500)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (month)

There is no clear preference for a certain home location where the horse would tend to spend the night. 

Instead of spliting by date, we can also specify a minimum movement speed and then split the continuous observation when this minimum speed is not reached for a certain time:

In [32]:
moving = mpd.TrajectoryCollection(traj.df[traj.df['speed'] > 0.05], 'CollarID')
moving = mpd.ObservationGapSplitter(moving).split(gap=timedelta(minutes=70))

In [33]:
moving.get_start_locations().hvplot(c='month', geo=True, tiles='EsriImagery', color='red', width=500, height=500)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]

### 3.3 Trajectory length

In [34]:
daily_lengths = [traj.get_length() for traj in daily]
daily_t = [traj.get_start_time() for traj in daily]

In [35]:
daily_lengths = pd.DataFrame(daily_lengths, index=daily_t, columns=['length'])
daily_lengths.hvplot(title='Daily trajectory length')

:Curve   [index]   (length)

The length of the daily trajectories varies between 1.6 and 6.2 km. (It is worth noting that this has to be considered a lower bound of the movement due to the sparseness of the tracking data.)

The seasonal trends agree well with the previously discovered seasonal movement speed patterns: winter trajectories tend to be shorter than summer trajectories. 

### 3.4 Covered area

#### Method 1: Convex hulls around trajectory

In [36]:
daily_areas = [(traj.id, traj.to_crs(CRS(25832)).to_linestring().convex_hull.area/10000) for traj in daily]
daily_areas = pd.DataFrame(daily_areas, index=daily_t, columns=['id', 'area'])
daily_areas.hvplot(title='Daily covered area [ha]', y='area')

:Curve   [index]   (area)

#### Method 2: Buffered trajectory

In [37]:
daily_areas = [(traj.id, traj.to_crs(CRS(25832)).to_linestring().buffer(15).area/10000) for traj in daily]
daily_areas = pd.DataFrame(daily_areas, index=daily_t, columns=['id', 'area'])
daily_areas.hvplot(title='Daily covered area [ha]', y='area')

:Curve   [index]   (area)

The ten smallest areas are:

In [38]:
daily_areas.sort_values(by='area')[:10]

id      area
2019-11-07 00:00:09  30788_2019-11-07 00:00:00  0.666244
2018-11-19 00:00:39  30788_2018-11-19 00:00:00  1.245522
2018-11-14 12:30:08  30788_2018-11-14 00:00:00  2.039815
2019-05-12 00:00:39  30788_2019-05-12 00:00:00  2.856620
2019-05-13 00:00:08  30788_2019-05-13 00:00:00  3.282696
2019-02-04 00:00:09  30788_2019-02-04 00:00:00  3.922588
2019-02-10 00:00:40  30788_2019-02-10 00:00:00  4.179243
2019-02-13 00:00:39  30788_2019-02-13 00:00:00  4.328685
2019-03-07 00:00:09  30788_2019-03-07 00:00:00  4.336160
2019-02-22 00:00:10  30788_2019-02-22 00:00:00  4.380967

The days with the smallest areas cover areas include the first and the last observation day (since they are only partially recorded). We can remove those:

In [39]:
daily_areas = daily_areas.drop(datetime(2018,11,14,12,30,8))
daily_areas = daily_areas.drop(datetime(2019,11,7,0,0,9))

The smallest area for a complete day was observed on 2018-11-19 with only 1.2 ha:

In [40]:
a = None
for i in daily_areas.sort_values(by='area')[:3].id:
    traj = daily.get_trajectory(i)
    if a: a = a + traj.hvplot(title=i, c='speed', line_width=2, cmap='RdYlBu', width=300, height=300)
    else: a = traj.hvplot(title=i, c='speed', line_width=2, cmap='RdYlBu', width=300, height=300)
a    

:Layout
   .Overlay.I   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.II  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)
   .Overlay.III :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)

## 3.5 Stop detection

Instead of splitting the continuous track into daily trajectories, an alternative approach is to split it at stops. Stops can be defined as parts of the track where the moving object stays within a small area for a certain duration. 

Let's have a look at movement of one day and how stop detection parameter settings affect the results:

In [41]:
MAX_DIAMETER = 100
MIN_DURATION = timedelta(hours=3)

one_day = daily.get_trajectory('30788_2018-11-17 00:00:00')
one_day_stops = mpd.TrajectoryStopDetector(one_day).get_stop_segments(
    min_duration=MIN_DURATION, max_diameter=MAX_DIAMETER)

( one_day.hvplot(title='Stops in Trajectory {}'.format(one_day.id), line_width=7.0, color='slategray', width=500) * 
 one_day_stops.hvplot(size=200, line_width=7, tiles=None, color='deeppink') *
 one_day_stops.get_start_locations().hvplot(geo=True, size=200, color='deeppink') )

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Path.I   :Path   [Longitude,Latitude]
   .Path.II  :Path   [Longitude,Latitude]
   .Path.III :Path   [Longitude,Latitude]
   .Points.I :Points   [Longitude,Latitude]

Let's apply stop detection to the whole dataset:

In [42]:
%%time
stops = mpd.TrajectoryStopDetector(tc).get_stop_segments(min_duration=MIN_DURATION, max_diameter=MAX_DIAMETER)
len(stops)

Wall time: 14.8 s


377

The spatial distribution reveals preferred stop locations:

In [43]:
stops.get_start_locations().hvplot(geo=True, tiles='OSM', color='deeppink', size=MAX_DIAMETER, alpha=0.2, width=500)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]

In [44]:
stop_durations = [stop.get_duration().seconds/3600.0 for stop in stops]
stop_durations = pd.DataFrame(stop_durations, columns=['duration'])
stop_durations.hvplot.hist(title='Stop duration histogram', xlabel='Duration [hours]', ylabel='n', bins=30)

:Histogram   [duration]   (duration_count)

## 4. Exploring patterns in trajectory and event data

The fourth exploration step looks at the set of all or subsets of the trajectories and events extracted from the movement data. This step commonly involves many of the computationally more expensive operations, such as trajectory similarity computations. 

TODO

## 5. Analyzing outliers

The ﬁfth and ﬁnal exploration steps looks at potential outliers and how they may
challenge preconceived assumptions about the dataset characteristics. This step in
particular regularly requires domain knowledge that exceeds the information that
can be discovered from the movement data itself. 

TODO

## Conclusion

TODO

## Continue exploring MovingPandas


1. [Ship data analysis](2-ship-data.ipynb)
2. [Bird migration analysis](1-bird-migration.ipynb)
3. [Horse collar data exploration](3-horse-collar.ipynb)
4. [Stop hotspot detection](4-stop-hotspots.ipynb)